In [2]:
import pandas as pd
import os

In [3]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "rentals/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [26]:
# base cols RegionID,SizeRank,RegionName,RegionType,StateName


data_frames = []

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        # print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))
        exclude_columns = [
            "RegionID",
            "SizeRank",
            "RegionName",
            "RegionType",
            "StateName",
            "Home Type",
        ]

        if "_sfrcondomfr_" in filename:
            cur_df["Home Type"] = "all homes plus multifamily"
            # change column type to string
            cur_df["RegionName"] = cur_df["RegionName"].astype(str)
            if "City" in filename:
                exclude_columns = [
                    "RegionID",
                    "SizeRank",
                    "RegionName",
                    "RegionType",
                    "StateName",
                    "Home Type",
                    # City Specific
                    "State",
                    "Metro",
                    "CountyName",
                ]
            elif "Zip" in filename:
                exclude_columns = [
                    "RegionID",
                    "SizeRank",
                    "RegionName",
                    "RegionType",
                    "StateName",
                    "Home Type",
                    # Zip Specific
                    "State",
                    "City",
                    "Metro",
                    "CountyName",
                ]
            elif "County" in filename:
                exclude_columns = [
                    "RegionID",
                    "SizeRank",
                    "RegionName",
                    "RegionType",
                    "StateName",
                    "Home Type",
                    # County Specific
                    "State",
                    "Metro",
                    "StateCodeFIPS",
                    "MunicipalCodeFIPS",
                ]

        elif "_sfr_" in filename:
            cur_df["Home Type"] = "SFR"
        elif "_mfr_" in filename:
            cur_df["Home Type"] = "multifamily"

        # Identify columns to pivot
        columns_to_pivot = [col for col in cur_df.columns if col not in exclude_columns]

        smoothed = "_sm_" in filename
        seasonally_adjusted = "_sa_" in filename

        col_name = "Rent"
        if smoothed:
            col_name += " (Smoothed)"
        if seasonally_adjusted:
            col_name += " (Seasonally Adjusted)"
        cur_df = pd.melt(
            cur_df,
            id_vars=exclude_columns,
            value_vars=columns_to_pivot,
            var_name="Date",
            value_name=col_name,
        )
        data_frames.append(cur_df)
        # print(filename)


def get_combined_df(data_frames):
    combined_df = None
    if len(data_frames) > 1:
        # iterate over dataframes and merge or concat
        combined_df = data_frames[0]
        for i in range(1, len(data_frames)):
            cur_df = data_frames[i]
            combined_df = pd.merge(
                combined_df,
                cur_df,
                on=[
                    "RegionID",
                    "SizeRank",
                    "RegionName",
                    "RegionType",
                    "StateName",
                    "Home Type",
                    "Date",
                ],
                how="outer",
                suffixes=("", "_" + str(i)),
            )
    elif len(data_frames) == 1:
        combined_df = data_frames[0]

    return combined_df


combined_df = get_combined_df(data_frames)


# iterate over rows of combined df and coalesce column values across columns that start with "Median Sale Price"
columns_to_coalesce = ["Rent (Smoothed)", "Rent (Smoothed) (Seasonally Adjusted)"]

for index, row in combined_df.iterrows():
    for col in combined_df.columns:
        for column_to_coalesce in columns_to_coalesce:
            if column_to_coalesce in col and "_" in col:
                if not pd.isna(row[col]):
                    combined_df.at[index, column_to_coalesce] = row[col]

# remove columns with underscores
combined_df = combined_df[[col for col in combined_df.columns if "_" not in col]]


combined_df

RegionID  SizeRank   RegionName RegionType StateName  \
0              66       146   Ada County     county        ID   
1              66       146   Ada County     county        ID   
2              66       146   Ada County     county        ID   
3              66       146   Ada County     county        ID   
4              66       146   Ada County     county        ID   
...           ...       ...          ...        ...       ...   
1258735    857850       713  Cherry Hill       city        NJ   
1258736    857850       713  Cherry Hill       city        NJ   
1258737    857850       713  Cherry Hill       city        NJ   
1258738    857850       713  Cherry Hill       city        NJ   
1258739    857850       713  Cherry Hill       city        NJ   

                          Home Type State           Metro  StateCodeFIPS  \
0        all homes plus multifamily    ID  Boise City, ID           16.0   
1        all homes plus multifamily    ID  Boise City, ID           16.0   
2        all homes plus multifamily    ID  Boise City, ID           16.0   
3        all homes plus multifamily    ID  Boise City, ID           16.0   
4        all homes plus multifamily    ID  Boise City, ID           16.0   
...                             ...   ...             ...            ...   
1258735  all homes plus multifamily   NaN             NaN            NaN   
1258736  all homes plus multifamily   NaN             NaN            NaN   
1258737  all homes plus multifamily   NaN             NaN            NaN   
1258738  all homes plus multifamily   NaN             NaN            NaN   
1258739  all homes plus multifamily   NaN             NaN            NaN   

         MunicipalCodeFIPS        Date  Rent (Smoothed)     CountyName  \
0                      1.0  2015-01-31       927.493763            NaN   
1                      1.0  2015-02-28       931.690623            NaN   
2                      1.0  2015-03-31       932.568601            NaN   
3                      1.0  2015-04-30       933.148134            NaN   
4                      1.0  2015-05-31       941.045724            NaN   
...                    ...         ...              ...            ...   
1258735                NaN  2023-08-31      2291.604800  Camden County   
1258736                NaN  2023-09-30      2296.188906  Camden County   
1258737                NaN  2023-10-31      2292.270938  Camden County   
1258738                NaN  2023-11-30      2253.417140  Camden County   
1258739                NaN  2023-12-31      2280.830303  Camden County   

         Rent (Smoothed) (Seasonally Adjusted) City  
0                                   927.493763  NaN  
1                                   931.690623  NaN  
2                                   932.568601  NaN  
3                                   933.148134  NaN  
4                                   941.045724  NaN  
...                                        ...  ...  
1258735                            2244.961006  NaN  
1258736                            2254.213172  NaN  
1258737                            2261.540446  NaN  
1258738                            2257.956024  NaN  
1258739                            2280.830303  NaN  

[1258740 rows x 15 columns]

In [27]:
combined_df.columns
# combined_df["RegionType"].unique()

# combined_df

Index(['RegionID', 'SizeRank', 'RegionName', 'RegionType', 'StateName',
       'Home Type', 'State', 'Metro', 'StateCodeFIPS', 'MunicipalCodeFIPS',
       'Date', 'Rent (Smoothed)', 'CountyName',
       'Rent (Smoothed) (Seasonally Adjusted)', 'City'],
      dtype='object')

In [32]:
final_df = combined_df

for index, row in final_df.iterrows():
    if row["RegionType"] == "city":
        final_df.at[index, "City"] = row["RegionName"]
    elif row["RegionType"] == "county":
        final_df.at[index, "County"] = row["RegionName"]

# coalesce State and StateName columns
final_df["State"] = final_df["State"].combine_first(final_df["StateName"])
final_df["State"] = final_df["County"].combine_first(final_df["CountyName"])

final_df = final_df.drop(columns=["StateName", "CountyName"])
final_df

RegionID  SizeRank   RegionName RegionType  \
0              66       146   Ada County     county   
1              66       146   Ada County     county   
2              66       146   Ada County     county   
3              66       146   Ada County     county   
4              66       146   Ada County     county   
...           ...       ...          ...        ...   
1258735    857850       713  Cherry Hill       city   
1258736    857850       713  Cherry Hill       city   
1258737    857850       713  Cherry Hill       city   
1258738    857850       713  Cherry Hill       city   
1258739    857850       713  Cherry Hill       city   

                          Home Type          State           Metro  \
0        all homes plus multifamily     Ada County  Boise City, ID   
1        all homes plus multifamily     Ada County  Boise City, ID   
2        all homes plus multifamily     Ada County  Boise City, ID   
3        all homes plus multifamily     Ada County  Boise City, ID   
4        all homes plus multifamily     Ada County  Boise City, ID   
...                             ...            ...             ...   
1258735  all homes plus multifamily  Camden County             NaN   
1258736  all homes plus multifamily  Camden County             NaN   
1258737  all homes plus multifamily  Camden County             NaN   
1258738  all homes plus multifamily  Camden County             NaN   
1258739  all homes plus multifamily  Camden County             NaN   

         StateCodeFIPS  MunicipalCodeFIPS        Date  Rent (Smoothed)  \
0                 16.0                1.0  2015-01-31       927.493763   
1                 16.0                1.0  2015-02-28       931.690623   
2                 16.0                1.0  2015-03-31       932.568601   
3                 16.0                1.0  2015-04-30       933.148134   
4                 16.0                1.0  2015-05-31       941.045724   
...                ...                ...         ...              ...   
1258735            NaN                NaN  2023-08-31      2291.604800   
1258736            NaN                NaN  2023-09-30      2296.188906   
1258737            NaN                NaN  2023-10-31      2292.270938   
1258738            NaN                NaN  2023-11-30      2253.417140   
1258739            NaN                NaN  2023-12-31      2280.830303   

         Rent (Smoothed) (Seasonally Adjusted)         City      County  
0                                   927.493763          NaN  Ada County  
1                                   931.690623          NaN  Ada County  
2                                   932.568601          NaN  Ada County  
3                                   933.148134          NaN  Ada County  
4                                   941.045724          NaN  Ada County  
...                                        ...          ...         ...  
1258735                            2244.961006  Cherry Hill         NaN  
1258736                            2254.213172  Cherry Hill         NaN  
1258737                            2261.540446  Cherry Hill         NaN  
1258738                            2257.956024  Cherry Hill         NaN  
1258739                            2280.830303  Cherry Hill         NaN  

[1258740 rows x 14 columns]

In [33]:
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateCodeFIPS": "State Code FIPS",
        "MunicipalCodeFIPS": "Municipal Code FIPS",
    }
)

final_df

Region ID  Size Rank       Region Region Type  \
0               66        146   Ada County      county   
1               66        146   Ada County      county   
2               66        146   Ada County      county   
3               66        146   Ada County      county   
4               66        146   Ada County      county   
...            ...        ...          ...         ...   
1258735     857850        713  Cherry Hill        city   
1258736     857850        713  Cherry Hill        city   
1258737     857850        713  Cherry Hill        city   
1258738     857850        713  Cherry Hill        city   
1258739     857850        713  Cherry Hill        city   

                          Home Type          State           Metro  \
0        all homes plus multifamily     Ada County  Boise City, ID   
1        all homes plus multifamily     Ada County  Boise City, ID   
2        all homes plus multifamily     Ada County  Boise City, ID   
3        all homes plus multifamily     Ada County  Boise City, ID   
4        all homes plus multifamily     Ada County  Boise City, ID   
...                             ...            ...             ...   
1258735  all homes plus multifamily  Camden County             NaN   
1258736  all homes plus multifamily  Camden County             NaN   
1258737  all homes plus multifamily  Camden County             NaN   
1258738  all homes plus multifamily  Camden County             NaN   
1258739  all homes plus multifamily  Camden County             NaN   

         State Code FIPS  Municipal Code FIPS        Date  Rent (Smoothed)  \
0                   16.0                  1.0  2015-01-31       927.493763   
1                   16.0                  1.0  2015-02-28       931.690623   
2                   16.0                  1.0  2015-03-31       932.568601   
3                   16.0                  1.0  2015-04-30       933.148134   
4                   16.0                  1.0  2015-05-31       941.045724   
...                  ...                  ...         ...              ...   
1258735              NaN                  NaN  2023-08-31      2291.604800   
1258736              NaN                  NaN  2023-09-30      2296.188906   
1258737              NaN                  NaN  2023-10-31      2292.270938   
1258738              NaN                  NaN  2023-11-30      2253.417140   
1258739              NaN                  NaN  2023-12-31      2280.830303   

         Rent (Smoothed) (Seasonally Adjusted)         City      County  
0                                   927.493763          NaN  Ada County  
1                                   931.690623          NaN  Ada County  
2                                   932.568601          NaN  Ada County  
3                                   933.148134          NaN  Ada County  
4                                   941.045724          NaN  Ada County  
...                                        ...          ...         ...  
1258735                            2244.961006  Cherry Hill         NaN  
1258736                            2254.213172  Cherry Hill         NaN  
1258737                            2261.540446  Cherry Hill         NaN  
1258738                            2257.956024  Cherry Hill         NaN  
1258739                            2280.830303  Cherry Hill         NaN  

[1258740 rows x 14 columns]

In [35]:
if not os.path.exists(FULL_PROCESSED_DIR_PATH):
    os.makedirs(FULL_PROCESSED_DIR_PATH)

final_df.to_json(FULL_PROCESSED_DIR_PATH + "final.jsonl", orient="records", lines=True)